In [1]:
%run "10_Data into model format.ipynb"
version = 'model20220822_4x8fsplit_seed10'
#n=1#100
data_seed = 10
n_splits = 8
colseed_set = [11,19,10,9]
isclear_memory = 1
major_save_path = Huge_data_path+'Model/'+version
apply_item_save_path = major_save_path+'/applied_items.pkl'

function: load_DProcessed_df(file), amex_metric(y_true, y_pred), file_get(dataset,version,dataset_list,num_list_inModel,ignore_list)
list:all_cols,cat_list,num_list , varible: Huge_data_path


In [2]:

try:
    os.mkdir(major_save_path)
    os.mkdir(major_save_path+'/models')
    os.mkdir(major_save_path+'/val_pred')
    os.mkdir(major_save_path+'/sub')
except:
    1
params = {
'objective':'binary',
#'boosting': 'dart',
'random_state': 19,
"num_leaves": 160,#130
#'max_depth':8,
'learning_rate': 0.01,
'colsample_bytree': 0.19,
'n_estimators': 10000,
#'max_bins': 60,
'importance_type':'gain',
'min_child_samples':50,
'early_stopping_round':500,
'reg_lambda':2,
'n_jobs':8,
#'device':'gpu',
             }
collect_list = pd.read_csv('Data/p_important_fulllist.csv',index_col=0)
reference_lv = pd.read_csv('Data/important_scoresplit.csv',index_col=0)
applied_items = dict()
record_df = pd.DataFrame()
needed_item = list()


for dataset_word in collect_list['dataset_word'].unique():
    if dataset_word =='cat__WoEonlylast_baseset_WoE':
        continue
    try:
        needed_item =list(needed_item+list(collect_list[(collect_list['dataset_word']==dataset_word) & (collect_list['r'] > 0)].index))#reference_lv.loc[dataset_word,'mid']
    except:
        print(dataset_word, 'skipped')
        continue

needed_item =list(set(needed_item+['period_count']))
print(len(needed_item))
needed_item = [col for col in needed_item if col not in drop_list]
needed_item.sort()
print(len(needed_item))

data_df = file_getII('train','na',dataset_list,needed_item,catset_list)
needed_item = list(set([col for col in data_df.columns if col != 'target']))
print(len(needed_item))
feature_trail = dict()
temp_df = data_df[needed_item]
i = 0
for seed in colseed_set:
    kf = KFold(n_splits=n_splits, random_state=seed, shuffle=True)
    for train_index, test_index in kf.split(list(needed_item)):
        feature_trail[i] = list(set(fix_item +list(temp_df.columns[test_index])))
        i +=1
del temp_df
gc.collect()

3280
3164
3163


0

In [3]:


for i in range(len(colseed_set)*n_splits):
    print(i)
    model_save_path = major_save_path+'/models/m'+str(i)+'.mdl'
    needed_item =feature_trail[i]
    #data_df = fulldata_df[list(needed_item)+['target']]

    x_train, x_valid, y_train, y_valid = train_test_split(data_df[list(needed_item)],data_df['target'], #
                                                        test_size=0.2,random_state=data_seed)

    applied_items[str(i)] = list(x_train.columns)
    model = lgbm.LGBMClassifier(**params)
    model.fit(x_train,y_train,eval_set=[(x_valid, y_valid)],)
    model.booster_.save_model(model_save_path)


    #performance record
    model = lgbm.Booster(model_file=model_save_path)

    train_info = pd.DataFrame()
    train_info['prediction_train'] = model.predict(x_train)
    train_info['target'] = y_train.reset_index(drop=True)
    train_g,train_d,train_score,a = amex_metric(train_info['target'].astype(int), train_info['prediction_train'])
    #print(train_g,train_d,train_score)

    val_info = pd.DataFrame()
    val_info['prediction_test'] = model.predict(x_valid)
    val_info['customer_ID'] = y_valid.index
    val_info = val_info.set_index('customer_ID')
    val_info = pd.concat([val_info,y_valid,],axis=1)
    test_g,test_d,test_score,a = amex_metric(val_info['target'].astype(int), val_info['prediction_test'])
    #print(test_g,test_d,test_score)

    feature_imp_df = pd.DataFrame(model.feature_importance(),index=model.feature_name(),columns=['feature_important']).sort_values('feature_important',ascending=False)
    top_item = feature_imp_df.iloc[0].name
    needed_item = list(feature_imp_df.iloc[1:].index) #for next iteration

    record_dict = {'th':str(i),'time':datetime.datetime.now().strftime("%m/%d/%Y %H:%M:%S"),
    'train_g':train_g,'train_d':train_d,'train_score':train_score,
    'test_g':test_g,'test_d':test_d,'test_score':test_score,
    'model_params':params,'top_item':top_item,#'note':note,
    }
    record_df = pd.concat([record_df,pd.DataFrame(record_dict,index=['new'])])#,ignore_index=True)
    val_info.to_csv(major_save_path+'/val_pred/v'+str(i)+'.csv')
    record_df.to_csv(major_save_path +'/preformace_record.csv',index=False)
    pk.dump(applied_items,open(major_save_path+"/applied_items.pkl","wb"))


0
[1]	valid_0's binary_logloss: 0.567825
[2]	valid_0's binary_logloss: 0.562714
[3]	valid_0's binary_logloss: 0.558033
[4]	valid_0's binary_logloss: 0.553275
[5]	valid_0's binary_logloss: 0.548702
[6]	valid_0's binary_logloss: 0.544161
[7]	valid_0's binary_logloss: 0.539811
[8]	valid_0's binary_logloss: 0.53561
[9]	valid_0's binary_logloss: 0.531453
[10]	valid_0's binary_logloss: 0.527079
[11]	valid_0's binary_logloss: 0.522747
[12]	valid_0's binary_logloss: 0.518828
[13]	valid_0's binary_logloss: 0.514884
[14]	valid_0's binary_logloss: 0.511099
[15]	valid_0's binary_logloss: 0.5071
[16]	valid_0's binary_logloss: 0.503175
[17]	valid_0's binary_logloss: 0.49952
[18]	valid_0's binary_logloss: 0.495994
[19]	valid_0's binary_logloss: 0.492346
[20]	valid_0's binary_logloss: 0.488701
[21]	valid_0's binary_logloss: 0.485218
[22]	valid_0's binary_logloss: 0.481707
[23]	valid_0's binary_logloss: 0.478293
[24]	valid_0's binary_logloss: 0.475183
[25]	valid_0's binary_logloss: 0.471923
[26]	valid_

In [4]:
if isclear_memory == 1:
    del data_df,x_train, x_valid, y_train, y_valid
    gc.collect()

In [6]:
#sub result base on model
applied_items = pk.load(open(major_save_path+"/applied_items.pkl","rb"))
#needed_item = applied_items['0']
#test_df = file_getII('test','na',dataset_list,needed_item,catset_list)#ignore_list
sub_pre = pd.read_csv('Data/sample_submission.csv',index_col=0)
for i in range(len(colseed_set)*n_splits):
    needed_item =applied_items[str(i)]
    test_df = file_getII('test','na',dataset_list,needed_item,catset_list)#ignore_list


    test_df = test_df[[col  for col in needed_item if col != 'target']]
    model_save_path = major_save_path+'/models/m'+str(i)+'.mdl'
    model = lgbm.Booster(model_file=model_save_path)


    y_info = pd.DataFrame()
    y_info['customer_ID']= test_df.index
    y_info['prediction'] = model.predict(test_df)
    y_info = sub_pre.drop('prediction',axis=1).join(y_info.set_index('customer_ID'), on='customer_ID')

    
    y_info.to_csv(major_save_path+'/sub/'+'subm'+str(i)+'.zip', compression={'method': 'zip', 'archive_name': 'subm'+str(i)+'.csv'})
    print(version,i,end="\r", flush=True)

In [5]:
#Vaildation score
sub_pre = pd.read_csv(major_save_path+'/val_pred/'+'v'+str(0)+'.csv',index_col=0)
sub_pre['prediction_test'] = 0
for i in range(len(colseed_set)*n_splits):
    sub_pre1 =pd.read_csv(major_save_path+'/val_pred/'+'v'+str(i)+'.csv',index_col=0)
    sub_pre['prediction_test'] = sub_pre['prediction_test']+sub_pre1['prediction_test']/(len(colseed_set)*n_splits)

test_g,test_d,test_score,a = amex_metric(sub_pre['target'].astype(int), sub_pre['prediction_test'])
print(test_g,test_d,test_score)

0.9234985263118671 0.6596422137500524 79.15703700309598


In [7]:
sub_pre = pd.read_csv('Data/sample_submission.csv',index_col=0)
sub_pre['prediction'] = 0
for i in range(len(colseed_set)*n_splits):
    sub_pre1 =pd.read_csv(major_save_path+'/sub/'+'subm'+str(i)+'.zip').set_index('customer_ID')
    sub_pre['prediction'] = sub_pre['prediction']+sub_pre1['prediction']/(len(colseed_set)*n_splits)
sub_pre.to_csv(major_save_path+'/sub/fullmerge.zip')


In [8]:
sub_pre = pd.read_csv(major_save_path+'/sub/fullmerge.zip',index_col=0)
sub_pre = (sub_pre+pd.read_csv(Huge_data_path+'Model/'+'model20220820_4x8fsplit_seed19/sub/fullmerge.zip',index_col=0))/2
sub_pre.to_csv(major_save_path+'/sub/mergewith_model20220820_4x8fsplit_seed19.zip')
sub_pre

prediction
customer_ID                                                   
00000469ba478561f23a92a868bd366de6f6527a684c9a2...    0.026807
00001bf2e77ff879fab36aa4fac689b9ba411dae63ae397...    0.000931
0000210045da4f81e5f122c6bde5c2a617d03eef67f82c5...    0.022863
00003b41e58ede33b8daf61ab56d9952f17c9ad1c3976cf...    0.188167
00004b22eaeeeb0ec976890c1d9bfc14fd9427e98c4ee9a...    0.833027
...                                                        ...
ffff952c631f2c911b8a2a8ca56ea6e656309a83d2f64c5...    0.013380
ffffcf5df59e5e0bba2a5ac4578a34e2b5aa64a1546cd3a...    0.870710
ffffd61f098cc056dbd7d2a21380c4804bbfe60856f475c...    0.557371
ffffddef1fc3643ea179c93245b68dca0f36941cd839778...    0.310416
fffffa7cf7e453e1acc6a1426475d5cb9400859f82ff61c...    0.039837

[924621 rows x 1 columns]

In [19]:

first_val_file = ''#Huge_data_path+'Model/'+'model20220816_hldart_over0/'+'val_pred/v0.csv'
update_count = 100
#cut_list = [0,0.002,0.003,0.004,0.005,0.01,0.05,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,0.95,0.96,0.97,0.98,0.99,1]
##############cut info##########################
cut_list_dict = {0:[0,0.002,0.003,0.004,0.005,0.01,0.05,
0.1,0.15,0.2,0.25,0.3,0.35,0.4,0.45,0.5,0.55,0.6,0.65,0.7,0.75,0.8,0.85,0.9,
0.95,0.96,0.97,0.98,0.99,1],
1:[0,0.002,0.003,0.004,0.005,0.01,0.05,
0.125,0.175,0.225,0.275,0.325,0.375,0.425,0.475,0.525,0.575,0.625,0.675,0.725,0.775,0.825,0.875,0.925,
0.95,0.96,0.97,0.98,0.99,1]}
version1 = 'major'; version2 = 'new'
record_df = pd.DataFrame()
record_dfinmodel = pd.read_csv(major_save_path +'/preformace_record.csv')
score_ref = record_dfinmodel['test_score'][0]


##############prepare val_major file##########################
for i in range(len(colseed_set)*n_splits):
    if len(first_val_file) >0:
        val_info1 = pd.read_csv(first_val_file)
        target = val_info1[['target']]#,'customer_ID']]
        cust_ID = val_info1[['customer_ID']]
        first_val_file = '' #clean the if loop
    elif (i == 0):
        val_info1 = pd.read_csv(major_save_path+'/val_pred/v'+str(i)+'.csv')
        target = val_info1[['target']]#,'customer_ID']]
        cust_ID = val_info1[['customer_ID']]
        continue
    ##############prepare val_new file##########################
    val_info2 = pd.read_csv(major_save_path+'/val_pred/v'+str(i)+'.csv')


    ##############Define value_pointing ['anchor'] logic ##########################
    #share_value = 0 #np.clip(0.5-(score_ref-record_dfinmodel['test_score'][i])/0.003,0,0.5)
    def value_pointing(x1,x2,value,x1min,x1max,x2min,x2max):
        if (x1!=x2):
            if value > x1max:
                return np.clip((value-x1max)/(x2max-x1max),0,1)
            if value < x1min: 
                return np.clip((value-x1min)/(x2min-x1min),0,1)
    #   return none
    #    return share_value #0.5 for 2 model mean, 0 for always keep major(x1) model value

    ##############Set Prediction Groups ##########################
    anchor_df = pd.DataFrame()
    for cut_kth in cut_list_dict:
        cut_list = cut_list_dict[cut_kth]
        gplist = pd.cut(pd.DataFrame(cut_list[:-1])[0]+cut_list[1]*0.0001, cut_list).apply(lambda x: x.mid).unique().sort_values().astype('float32').round(5)
        gplist2 = np.array([])
    ##############prepare cut df##########################
        for j in range(len(gplist)):
            gplist2 = np.append(gplist2,gplist)
        gp_totest = pd.concat([pd.DataFrame(np.repeat(gplist, len(gplist)) , columns=['pred_gp_v1']),pd.DataFrame(gplist2 , columns=['pred_gp_v2'])],axis=1)
        val_info1['pred_gp'] =  pd.cut(val_info1["prediction_test"], cut_list).apply(lambda x: x.mid).astype('float32').round(5)
        val_info1['pred_gp_min'] =  pd.cut(val_info1["prediction_test"], cut_list).apply(lambda x: x.left).astype('float32').round(5)
        val_info1['pred_gp_max'] =  pd.cut(val_info1["prediction_test"], cut_list).apply(lambda x: x.right).astype('float32').round(5)

        val_info2['pred_gp'] =  pd.cut(val_info2["prediction_test"], cut_list).apply(lambda x: x.mid).astype('float32').round(5)
        val_info2['pred_gp_min'] =  pd.cut(val_info2["prediction_test"], cut_list).apply(lambda x: x.left).astype('float32').round(5)
        val_info2['pred_gp_max'] =  pd.cut(val_info2["prediction_test"], cut_list).apply(lambda x: x.right).astype('float32').round(5)

        val_info1 = pd.concat([val_info1[['prediction_test','pred_gp','pred_gp_min','pred_gp_max']].add_suffix('_'+version1),
                                val_info2[['prediction_test','pred_gp','pred_gp_min','pred_gp_max']].add_suffix('_'+version2)]
                                ,axis=1)
        
        val_info1 = pd.concat([val_info1,target],axis=1)
        val_info1['diff'] = val_info1['prediction_test_'+version1]-val_info1['prediction_test_'+version2]
        val_info1['check'] = (abs(val_info1['diff'])>(val_info1['pred_gp_max_'+version1]-val_info1['pred_gp_min_'+version1])/5)
        pre_gp_ref = ['pred_gp_'+version1,'pred_gp_min_'+version1,'pred_gp_max_'+version1,
                    'pred_gp_'+version2,'pred_gp_min_'+version2,'pred_gp_max_'+version2]
    
    
        ##############gp_inf for large prediction diff cases ##########################
        gp_inf = val_info1[val_info1['check']==True].groupby(pre_gp_ref).agg(['mean','count'])['target'].reset_index()
        gp_inf[pre_gp_ref] = gp_inf[pre_gp_ref].astype('float')

        gp_inf['anchor'] = gp_inf.apply(lambda x: 
                                        value_pointing(x['pred_gp_'+version1],x['pred_gp_'+version2],x['mean'],
                                        x['pred_gp_min_'+version1],x['pred_gp_max_'+version1],
                                        x['pred_gp_min_'+version2],x['pred_gp_max_'+version2]) 
                                        if x['count'] >= update_count else np.NaN
                                        , axis=1)
        
        #gp_totest = pd.read_csv('Model/predgp_inf/gp_sample.csv',index_col=0)#<--self gen
        gp_inf = gp_totest.merge(gp_inf,how='left',left_on=['pred_gp_v1','pred_gp_v2'],right_on=['pred_gp_'+version1,'pred_gp_'+version2])
        #gp_inf['anchor'] =gp_inf['anchor'].fillna(0)
        gp_inf['count'] =gp_inf['count'].fillna(0)
        gp_inf = gp_inf[['pred_gp_'+version1,'pred_gp_'+version2,'anchor','count']]
        gp_inf.to_pickle(major_save_path +'/val_pred/gp'+str(i)+'_'+str(cut_kth)+'.plk')
        
        val_info1 = val_info1.join(gp_inf.rename(columns = {'anchor':'anchor'+str(cut_kth)}).set_index(['pred_gp_'+version1,'pred_gp_'+version2,]),on=['pred_gp_'+version1,'pred_gp_'+version2,])
        val_info1['anchor'+str(cut_kth)] = val_info1.apply(lambda x: x['anchor'+str(cut_kth)] if x['check']==True else np.NAN,axis=1)
        anchor_df['anchor'+str(cut_kth)] = val_info1['anchor'+str(cut_kth)]
        val_info1 = val_info1.rename(columns={'prediction_test_'+version1:'prediction_test'})[['prediction_test','target']]



    ##############Apply ['anchor']s##########################
    val_info1 = pd.concat([val_info1[['prediction_test']].add_suffix('_'+version1),
                            val_info2[['prediction_test']].add_suffix('_'+version2)]
                            ,axis=1)
    val_info1 = pd.concat([val_info1,anchor_df],axis=1)
    
    val_info1['anchor'] = val_info1[[col for col in val_info1.columns if (col.startswith('anchor'))]].mean(axis=1)
    val_info1['anchor'] =val_info1['anchor'].fillna(0)
    val_info1['prediction_test'] = val_info1.apply(lambda x: x['prediction_test_'+version1]*(1-x['anchor'])+ x['prediction_test_'+version2]*(x['anchor'])
    #if x['count']>update_count else x['prediction_test_'+version1]
    ,axis=1)
    

    ##############return val_info1 into origal form ##########################
    val_info1 = pd.concat([val_info1,target],axis=1)
    val_info1 = pd.concat([val_info1,cust_ID],axis=1)
    val_info1 = val_info1[['customer_ID','prediction_test','target']]
    test_g,test_d,test_score,a = amex_metric(val_info1['target'].astype(int), val_info1['prediction_test'])

    record_dict = {'th':str(i),'time':datetime.datetime.now().strftime("%m/%d/%Y %H:%M:%S"),
    'test_score':test_score,'test_g':test_g,'test_d':test_d,
    #'share':share_value,
    }
    score_ref = max(score_ref,test_score)
    val_info1.to_csv(major_save_path+'/val_pred/v_gp'+str(i)+'.zip', compression={'method': 'zip', 'archive_name': 'v_gp'+str(i)+'.csv'})#'.csv')
    record_df = pd.concat([record_df,pd.DataFrame(record_dict,index=['new'])])#,ignore_index=True)
    record_df.to_csv(major_save_path +'/val_pred/preformace_record.csv',index=False)
    print(version,i,end="\r", flush=True)
    
#val_info1.to_csv(major_save_path +'/val_pred/modelgped.csv',index=False)

In [21]:
#sub result base on gped
first_sub_file = ''#Huge_data_path+'Model/'+'model20220816_hldart_over0/'+'sub/subm0.zip'
sub_pre = pd.read_csv('Data/sample_submission.csv',index_col=0)
for i in range(len(colseed_set)*n_splits):
    y_info = pd.read_csv(major_save_path+'/sub/'+'subm'+str(i)+'.zip')
###################Create first file###########################################
    if len(first_sub_file)>0:
        y_first = pd.read_csv(first_sub_file)
        sub_pre1 = sub_pre.drop('prediction',axis=1).join(y_first.set_index('customer_ID'), on='customer_ID')#.set_index('customer_ID')
        sub_pre1.to_csv(major_save_path+'/sub/'+'subgpf.zip')
        first_sub_file=''
    elif i == 0:
        sub_pre1 = sub_pre.drop('prediction',axis=1).join(y_info.set_index('customer_ID'), on='customer_ID')#.set_index('customer_ID')
        sub_pre1.to_csv(major_save_path+'/sub/'+'subgp'+str(i)+'.zip')
        continue
    
    sub_pre2 = sub_pre.drop('prediction',axis=1).join(y_info.set_index('customer_ID'), on='customer_ID')#.set_index('customer_ID')

    #2 model test prediction merge

    sub_pre1 = sub_pre1.merge(sub_pre2,left_index = True, right_index = True, suffixes=('', '_new'))
    sub_pre1['diff'] = abs(sub_pre1['prediction']-sub_pre1['prediction_new'])
    for cut_kth in cut_list_dict:
        cut_list = cut_list_dict[cut_kth]
        gp_inf = pd.read_pickle((major_save_path +'/val_pred/gp'+str(i)+'_'+str(cut_kth)+'.plk')).rename(columns = {'anchor':'anchor'+str(cut_kth)})

        sub_pre1['pred_gp_major'] = pd.cut(sub_pre1["prediction"], cut_list).apply(lambda x: x.mid).astype('float32').round(5)#(sub_pre1['prediction']*10).astype(int)
        sub_pre1['pred_gp_min_major'] =  pd.cut(sub_pre1["prediction"], cut_list).apply(lambda x: x.left).astype('float32').round(5)
        sub_pre1['pred_gp_max_major'] =  pd.cut(sub_pre1["prediction"], cut_list).apply(lambda x: x.right).astype('float32').round(5)
        sub_pre1['pred_gp_new'] = pd.cut(sub_pre1["prediction_new"], cut_list).apply(lambda x: x.mid).astype('float32').round(5)#(sub_pre1['prediction_new']*10).astype(int)
        sub_pre1['pred_gp_min_new'] =  pd.cut(sub_pre1["prediction_new"], cut_list).apply(lambda x: x.left).astype('float32').round(5)
        sub_pre1['pred_gp_max_new'] =  pd.cut(sub_pre1["prediction_new"], cut_list).apply(lambda x: x.right).astype('float32').round(5)
        
        sub_pre1['diff'] = sub_pre1['prediction']-sub_pre1['prediction_new']
        sub_pre1['check'] = (abs(sub_pre1['diff'])>(sub_pre1['pred_gp_max_major']-sub_pre1['pred_gp_min_major'])/5)

        sub_pre1 = sub_pre1.reset_index().merge(gp_inf,how='left',left_on=['pred_gp_major','pred_gp_new'],right_on=['pred_gp_major','pred_gp_new']).set_index('customer_ID')#['pred_gp_major','pred_gp_new']
        sub_pre1['anchor'+str(cut_kth)] = sub_pre1.apply(lambda x: x['anchor'+str(cut_kth)] if x['check']==True else np.NAN,axis=1)
        
        #sub_pre2['prediction'] = pd.concat([sub_pre2,sub_pre1],axis=1).max(axis=1)
        #sub_pre1[['prediction']].to_csv('../huge data source/AE/submission/gped_withanch_submission.csv')
    sub_pre1['anchor'] = sub_pre1[[col for col in sub_pre1.columns if (col.startswith('anchor'))]].mean(axis=1)
    sub_pre1['anchor'] = sub_pre1['anchor'].fillna(0)
    sub_pre1['prediction'] =  sub_pre1.apply(lambda x: x['prediction']*(1-x['anchor'])+ x['prediction_new']*(x['anchor']) ,axis=1)

    sub_pre1 = sub_pre1[['prediction']]
    sub_pre1.to_csv(major_save_path+'/sub/'+'subgp'+str(i)+'.zip')
    print(version,i,end="\r", flush=True)
    
sub_pre1

prediction
customer_ID                                                   
00000469ba478561f23a92a868bd366de6f6527a684c9a2...    0.022282
00001bf2e77ff879fab36aa4fac689b9ba411dae63ae397...    0.000490
0000210045da4f81e5f122c6bde5c2a617d03eef67f82c5...    0.017289
00003b41e58ede33b8daf61ab56d9952f17c9ad1c3976cf...    0.230316
00004b22eaeeeb0ec976890c1d9bfc14fd9427e98c4ee9a...    0.899930
...                                                        ...
ffff952c631f2c911b8a2a8ca56ea6e656309a83d2f64c5...    0.013829
ffffcf5df59e5e0bba2a5ac4578a34e2b5aa64a1546cd3a...    0.883942
ffffd61f098cc056dbd7d2a21380c4804bbfe60856f475c...    0.592863
ffffddef1fc3643ea179c93245b68dca0f36941cd839778...    0.296468
fffffa7cf7e453e1acc6a1426475d5cb9400859f82ff61c...    0.038719

[924621 rows x 1 columns]